In [13]:
from bokeh import plotting, io, models, palettes
from bokeh.layouts import layout
import numpy as np
import maxr
import h5py

io.output_notebook()

Loading BokehJS ...

#### Integrating given an explicity velocity function

Define a blinking vortex function

In [2]:
palette = palettes.Spectral4

In [3]:
from maxr.flow.blink import tick, tock, blink

period = 0.1
ts = np.linspace(0,1,500)
fig = plotting.figure(height=300)
fig.line(ts, tick(ts, period), legend='tick', color=palette[1])
fig.line(ts, tock(ts, period), legend='tock', color=palette[2])
io.show(fig)

In [4]:
flow = blink(gamma=1, period=0.5)

In [5]:
u, v = flow(0.25, 0.5, ts)
fig = plotting.figure(height=300)
fig.line(ts, u, legend='u', color=palette[0])
fig.line(ts, v, legend='v', color=palette[-1])
fig.legend.location = 'top_left'
io.show(fig)

We need to calculate the velocity divergence and time derivative at given points

#### Integrating given a velocity field from file

Given a velocity field generating function, calculate values from a grid and write out to file

In [17]:
fname = 'blink.hdf5'
time_res = 50 
spatial_res = 100
maxr.flow.from_function(flow, fname, 
                        xgrid=(-2, 2, spatial_res),
                        ygrid=(-2, 2, spatial_res),
                        tgrid=(0, 1, time_res))
flow = maxr.flow.Flow(fname)

Check that everything got made ok

In [7]:
flow.info()

du/dt (100, 100, 50)
du/dx (100, 100, 50)
du/dy (100, 100, 50)
dv/dt (100, 100, 50)
dv/dx (100, 100, 50)
dv/dy (100, 100, 50)
t (50,)
u (100, 100, 50)
v (100, 100, 50)
x (100,)
y (100,)


In [8]:
flow.data['u'][..., 5]

array([[-0.04882455, -0.04977692, -0.05073962, ..., -0.03097222,
        -0.0303647 , -0.02977107],
       [-0.0490949 , -0.0500782 , -0.0510732 , ..., -0.03084741,
        -0.03023255, -0.02963214],
       [-0.04935266, -0.05036777, -0.05139605, ..., -0.0307079 ,
        -0.03008597, -0.02947903],
       ...,
       [ 0.04935266,  0.05036777,  0.05139605, ...,  0.0307079 ,
         0.03008597,  0.02947903],
       [ 0.0490949 ,  0.0500782 ,  0.0510732 , ...,  0.03084741,
         0.03023255,  0.02963214],
       [ 0.04882455,  0.04977692,  0.05073962, ...,  0.03097222,
         0.0303647 ,  0.02977107]])

In [9]:
np.nanpercentile(flow.data['u'][..., 5], (10, 90))

array([-0.10580036,  0.10580036])

In [10]:
np.__version__

'1.14.5'

In [11]:
time_slice = 5

def plot_fields(self, time_slice, percentiles=None):
    """
    Plot fields for a given flow at a given time-slice
    
    Parameters:
        time_slice - the time slice to plot at
        percentiles - if not None, the contours are clipped at these values
    """
    # Sort out placement for the fields
    grid = flow.grid()
    xmin, xmax = grid[0][0, 0], grid[0][-1, -1]
    ymin, ymax = grid[1][0, 0], grid[1][-1, -1]
    grid_kwargs = {'x': xmin, 'y': ymin, 'dw': xmax - xmin, 'dh': ymax - ymin}
    x_range = models.Range1d(xmin, xmax)
    y_range = models.Range1d(ymin, ymax)

    # Helper to make a figure
    fs = {}  # Will accumulate figures in here by key
    def get_figure(key):
        "Make and return a bokeh figure with all the right stuff set"
        fig = plotting.figure(width=200, height=200,
                              active_drag='pan', 
                              active_scroll='wheel_zoom')
        fig.title.text = key
        fig.toolbar.logo = None
        fig.toolbar_location = None
        fig.x_range = x_range
        fig.y_range = y_range
        fs[key] = fig
        return fig
    
    # Helper to plot image with percentile clipping
    if percentiles is not None:
        def _clip(a):
            vmin, vmax = np.nanpercentile(a, percentiles)
            return np.clip(a, vmin, vmax)
    else:
        def _clip(a):
            return a

    # Actually plot the results
    for num in ('du', 'dv'):
        for denom in ('dx', 'dy', 'dt'):
            key = '{}/{}'.format(num, denom)
            img = _clip(self.data[key][..., time_slice])
            fig = get_figure(key)
            fig.image([img], palette=palettes.Viridis256, **grid_kwargs)
            
            
    # Add plots for u and v
    for key in ('u', 'v'):
        img = _clip(self.data[key][..., time_slice])
        fig = get_figure(key)
        fig.image([img], palette=palettes.Magma256, **grid_kwargs)

    # Construct plots
    all_plots = layout(children=[
        [fs[k] for k in ('u', 'du/dx', 'du/dy', 'du/dt')],
        [fs[k] for k in ('v', 'dv/dx', 'dv/dy', 'dv/dt')]
    ])
    return all_plots

In [12]:
io.show(plot_fields(flow, time_slice=15, percentiles=(1, 99)))

In [13]:
from scipy.integrate import solve_ivp
from scipy.interpolate import RegularGridInterpolator

# Construct an interpolator for our grid
velocity = RegularGridInterpolator(
    (flow.data['x'], flow.data['y'], flow.data['t']),
    np.asarray([flow.data['u'], flow.data['v']]).transpose(1, 2, 3, 0),
    fill_value=0, bounds_error=False
)

# Construct an event which is triggered when a particle leaves the flow bounds
get_range = lambda x: (x[0], x[-1])
xmin, xmax = get_range(flow.data['x'])
ymin, ymax = get_range(flow.data['y'])
tmin, tmax = get_range(flow.data['t'])
escape = lambda _, y: np.maximum(
    (y[0] - xmin) * (y[0] - xmax),
    (y[1] - ymin) * (y[1] - ymax)
)
escape.terminal = True

We can also integrate neutrally buoyant particles in the flow

In [87]:
from tqdm import tqdm

# Make a small grid of points to warp
resolution = 37
width, height, x_centre, y_centre = 0.01, 1, 0, 0.1
xxs, yys = np.meshgrid(np.linspace(x_centre - width / 2, x_centre + width / 2, resolution), 
                       np.linspace(y_centre - height / 2, y_centre + height / 2, resolution))
npoints = np.product(xxs.shape)

# Integrate point positions
t_span, t_samples = (0, 50), 1000
flow = blink(gamma=1, period=0.5)
lines = []
for y0 in tqdm(zip(xxs.ravel(), yys.ravel()), 
               total=npoints, desc='Calculating streamlines'):
    result = solve_ivp(
        fun = lambda t, y: flow(y[0], y[1], t),
        t_span=t_span,
        y0=y0,
        t_eval=np.linspace(*t_span, num=t_samples),
        events=escape
    )
    if result.success:
        lines.append(result.y)
    else:
        print("Streamline couldn't be integrated")

Calculating streamlines: 100%|██████████| 1369/1369 [07:48<00:00,  2.92it/s]


In [90]:
# Map colors to points
palette = palettes.Viridis256
indices = (255 * (yys - y_centre - height / 2) / (height)).astype(int) - 1
colors = [palette[i] for i in indices.ravel()]

figures = []  # Will accumulate figures in here
x_range = models.Range1d(-1, 1)
y_range = models.Range1d(-0.5, 0.5)
def get_figure():
    "Make and return a bokeh figure with all the right stuff set"
    fig = plotting.figure(width=400, height=200,
                          active_drag='pan', 
                          active_scroll='wheel_zoom')
    fig.toolbar.logo = None
    fig.toolbar_location = None
    fig.x_range = x_range
    fig.y_range = y_range
    figures.append(fig)
    return fig

# Show points with varying time
for time in [int((t_samples - 1) * tfrac) for tfrac in np.linspace(0, 1, 30)]:
    fig = get_figure()
    fig.circle(*np.asarray([line[:, time] for line in lines]).transpose(),
               color=colors)
io.show(layout(figures))

And we can plot all the lines if we want to

In [17]:
fig = plotting.figure()
for line in lines:
    fig.line(*line)
io.show(fig)

In [18]:
def flow_forcing(f, r, w, t, params):
    """ Calculate the instantaneous terms using the flow forcing
    """
    R, S = params.R, params.S
    gx = (p.R - 1) * f('du/dt')(r) - numpy.dot(flow['u'] + w, ) - p.R / p.S * w
    

In [12]:
flow_forcing(
    numpy.array([-0.02, -0.02]), 
    numpy.array([0.02, 0.02]), 
    numpy.array([0, 0]))

TypeError: flow_forcing() missing 2 required positional arguments: 't' and 'params'

In [ ]:
def bashforth_adams(fs, ts):
    """ Integrate a function through time using a Bashforth-Adams method
    """
    